In [110]:
import json
f = open('./data/squall_final.json','r')
data = json.load(f)


In [111]:
## just run this to see that the data has titles and executions
title = 0
conv = 0
exe = 0
for d in data:
    if "title" in d.keys() and len(d['title']) > 0: title+=1
    if "converted_statement" in d.keys() and len(d['converted_statement']) > 0: conv+=1
    if "execute" in d.keys() and d['execute'] == True: exe+=1

print(title)
print(conv)
print(exe)

11276
11276
10633


In [114]:
import csv
import sqlite3, random
import editdistance, unidecode


executable = 0
count = 0
for d in data:
    count += 1
    print(count)
    if d['execute']:
        stmt = d['converted_statement']
#         print("converted stmt" , stmt)
        d['entailments'] = [stmt]
        d['contradictions'] = []
        sql_words = []
        for token in d['sql']:
            sql_words.append(token[1])
        final_selected_query = " ".join(sql_words)
#         print(final_selected_query)
#         print(d['sql'])
#         print("target ",str(d['tgt']))
        con = sqlite3.connect('./tables/db/' + d['tbl'] + '.db')
        cursor = con.cursor()
        try:
            num = int(d['tgt'])
            contra_choice = random.randint(max(0,num - 5), num + 5)
            if contra_choice != num:
                new_stm = stmt.replace(str(d['tgt']),str(contra_choice))
                d['contradictions'].append(new_stm)
            contra_choice = random.randint(max(0,num - 5), num + 5)
            if contra_choice != num:
                new_stm = stmt.replace(str(d['tgt']),str(contra_choice))
                d['contradictions'].append(new_stm)
        except:pass
        try:
            if not d['tgt'].isnumeric():
                col_token = []
                for token in d['sql']:
                    if token[0] == "Column" : 
                        col_token = token[1]
                        break
                cand_query = "select " + col_token + " from w"
                cursor.execute(cand_query)
                cand_ans = cursor.fetchall()
                cand_ans = [i[0].lower() for i in cand_ans]
                if d['tgt'].lower() in cand_ans:
                    cand_ans.remove(d['tgt'].lower())
                    cd = random.choice(cand_ans)
                    new_stm = stmt.replace(d['tgt'], cd)
                    d['contradictions'].append(new_stm)
                    cd = random.choice(cand_ans)
                    new_stm = stmt.replace(d['tgt'], cd)
                    d['contradictions'].append(new_stm)
                    
        except:pass
        for i in range(1,len(d['sql'])):
            try:
                token = d['sql'][i]
                word = token[1]
                if word[0] == "'" and word[-1] == "'" : word = word[1:-1]
                if token[0] == "Literal.String" and word.lower() in stmt.lower():
#                     print("string", token[1])
                    if d['sql'][i-2][0] == "Column":
                        colname = d['sql'][i-2][1].lower()
                        sel_query = "select " + colname + " from w"
                        cursor.execute(sel_query)
                        candidates = cursor.fetchall()
                        candidates = list(set(candidates))
                        candidates = random.sample(candidates, min(8,len(candidates)))
                        for candidate in candidates:
                            candidate = candidate[0]
                            if str(candidate) not in ['None','','-','N/A','n/a','TBD','—']:
#                                 print(candidate)
                                if "'" in candidate:
                                    new_query = final_selected_query.replace(word,word.lower()).replace("'" + word.lower() + "'",'"' + candidate.lower() + '"')
                                elif '"' in candidate:
                                    new_query = final_selected_query.replace(word,word.lower()).replace('"' + word.lower() + '"',"'" + candidate.lower() + "'")
                                else:
                                    new_query = final_selected_query.replace(word,word.lower()).replace(word.lower(),candidate.lower())
#                                 print(new_query)
                                cursor.execute(new_query)
                                new_ans = cursor.fetchall()
                                if len(new_ans) > 0:
                                    new_ans = str(new_ans[0][0])
                                    candidate = candidate.replace('\n',' ')
                                    new_entailment = stmt.lower().replace(d['tgt'], d['tgt'].lower()).replace(d['tgt'].lower(), new_ans).replace(word,word.lower()).replace(word.lower(),candidate).replace(".0 "," ")
                                    if new_entailment.lower() != stmt.lower() and (new_entailment not in d['entailments']) : d['entailments'].append(new_entailment)
                                    contra_cans = random.sample(candidates, min(3,len(candidates)))
                                    for can in contra_cans:
                                        can = can[0]
                                        if can not in ['','-','N/A','n/a','TBD','—']:
                                            if can != candidate:
                                                con_query = new_query.replace(candidate.lower(), can.lower())
                                                cursor.execute(con_query)
                                                con_ans = cursor.fetchall()
                                                if len(con_ans) > 0: con_ans = str(con_ans[0][0])
                                                if len(con_ans)==0 or con_ans != new_ans:
#                                                     print(new_ans, con_ans)
#                                                     print(new_query)
#                                                     print(con_query)
#                                                     print(new_entailment)
                                                    
                                                    new_contra = new_entailment.replace(candidate,candidate.lower()).replace(candidate.lower(),str(can)).replace(".0 "," ")
#                                                     print(new_contra)
                                                    if new_contra not in d['contradictions'] and new_contra.lower() != stmt: d['contradictions'].append(new_contra)
                if token[0] == "Literal.Number" and (" " + str(word) + " ") in stmt:
                    print("number ", str(token[1]))
                    if d['sql'][i-2][0] == "Column":
                        colname = d['sql'][i-2][1].lower()
                        sel_query = "select " + colname + " from w"
                        cursor.execute(sel_query)
                        candidates = cursor.fetchall()
                        candidates = list(set(candidates))
                        candidates = random.sample(candidates, min(8,len(candidates)))
                        word = " " + str(word) + " "
                        for candidate in candidates:
                            candidate = candidate[0]
                            if str(candidate) not in ['None','','-','N/A','n/a','TBD','—']:
                                new_query = final_selected_query.replace(str(word),str(" " + str(candidate) + " "))
                                cursor.execute(new_query)
                                new_ans = cursor.fetchall()
#                                 print("new ans, ", new_ans)
                                if len(new_ans) > 0:
                                    new_ans = str(new_ans[0][0])

                                    new_entailment = stmt.replace(str(d['tgt']), str(new_ans)).replace(str(word),str(" " + str(candidate) + " "))
        #                                 print("entail : ", new_entailment)
                                    if new_entailment.lower() != stmt.lower() and (new_entailment not in d['entailments']) : d['entailments'].append(new_entailment.replace(".0 "," "))
                                    contra_cans = random.sample(candidates, min(3,len(candidates)))
                                    for can in contra_cans:
                                        can = can[0]
                                        if str(can) not in ['None','','-','N/A','n/a','TBD','—']:
                                            can = " " + str(can) + " "
                                            if can != " " + str(candidate) + " ":
                                                con_query = new_query.replace(" " + str(candidate).lower() + " ", can.lower())
                                                cursor.execute(con_query)
                                                con_ans = cursor.fetchall()
                                      
                                                if len(con_ans) > 0: con_ans = str(con_ans[0][0])
                                                if len(con_ans)==0 or con_ans != new_ans:
                                                    new_contra = new_entailment.replace(" " + str(candidate) + " ",can)
                                                 
                                                    if new_contra not in d['contradictions'] and new_contra.lower() != stmt : d['contradictions'].append(new_contra.replace(".0 "," "))
                if token[0] == "Literal.Number" and (" " + str(word) + ".") in stmt:
                    print("number ", str(token[1]))
                    if d['sql'][i-2][0] == "Column":
                        colname = d['sql'][i-2][1].lower()
                        sel_query = "select " + colname + " from w"
                        cursor.execute(sel_query)
                        candidates = cursor.fetchall()
                        candidates = list(set(candidates))
                        candidates = random.sample(candidates, min(8,len(candidates)))
                        word = " " + str(word)
                        for candidate in candidates:
                            candidate = candidate[0]
                            if str(candidate) not in ['None','','-','N/A','n/a','TBD','—']:
                                new_query = final_selected_query.replace(str(word),str(" " + str(candidate)))
                                cursor.execute(new_query)
                                new_ans = cursor.fetchall()
#                                 print("new ans, ", new_ans)
                                if len(new_ans) > 0:
                                    new_ans = str(new_ans[0][0])

                                    new_entailment = stmt.replace(str(d['tgt']), str(new_ans)).replace(str(word),str(" " + str(candidate)))
        #                                 print("entail : ", new_entailment)
                                    if new_entailment.lower() != stmt.lower() and (new_entailment not in d['entailments']) : d['entailments'].append(new_entailment.replace(".0 "," "))
                                    contra_cans = random.sample(candidates, min(3,len(candidates)))
                                    for can in contra_cans:
                                        can = can[0]
                                        if str(can) not in ['None','','-','N/A','n/a','TBD','—']:
                                            can = " " + str(can)
                                            if can != " " + str(candidate):
                                                con_query = new_query.replace(" " + str(candidate).lower(), can.lower())
                                                cursor.execute(con_query)
                                                con_ans = cursor.fetchall()
                                                if len(con_ans) > 0: con_ans = str(con_ans[0][0])
                                                if len(con_ans)==0 or con_ans != new_ans:
                                                    new_contra = new_entailment.replace(" " + str(candidate),can)
            #                                             print("contra : ", new_contra)
                                                    if new_contra not in d['contradictions'] and new_contra.lower() != stmt : d['contradictions'].append(new_contra.replace(".0 "," "))
            except Exception as e:
                print(e)



1
number  1
number  2
2
3
near "higgins": syntax error
4
5
6
7
8
number  2005
number  2009
9
10
11
number  1965
12
number  1960
13
14
15
16
17
18
19
20
21
number  6
22
23
24
25
'NoneType' object has no attribute 'lower'
26
27
28
number  15
29
number  9
30
31
32
'NoneType' object has no attribute 'lower'
33
'NoneType' object has no attribute 'lower'
34
35
36
37
'NoneType' object has no attribute 'lower'
38
39
40
41
42
43
44
45
number  14
46
47
number  22
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
number  90
68
69
number  100
70
71
72
number  1900
73
number  30
74
75
76
77
78
79
80
number  135
81
82
number  2004
83
84
85
86
number  2014
87
88
89
90
91
92
93
94
number  2011
95
96
'NoneType' object has no attribute 'lower'
97
98
99
100
101
near "qali": syntax error
102
103
104
number  3
105
106
107
108
109
110
111
112
113
114
number  1999
115
116
117
118
119
120
121
number  1984
number  1988
122
number  1981
123
124
125
126
127
128
number  2010
129
number  2007
130
131
132

1131
1132
1133
number  17
1134
1135
1136
number  10
1137
number  2004
1138
number  2010
1139
1140
1141
1142
1143
1144
1145
1146
no such column: c3_list_maximum_number
1147
1148
1149
1150
1151
1152
number  17
1153
1154
1155
1156
1157
1158
1159
'NoneType' object has no attribute 'lower'
1160
1161
1162
1163
1164
1165
1166
number  2011
number  2011
1167
number  2011
1168
1169
1170
1171
1172
1173
1174
near "sewect": syntax error
1175
1176
1177
1178
number  0
1179
number  1
number  12
1180
near "c4_result": syntax error
1181
1182
1183
1184
1185
1186
1187
1188
1189
1190
1191
1192
1193
1194
1195
1196
near "s": syntax error
1197
number  2003
1198
1199
1200
1201
1202
1203
number  10
1204
1205
1206
1207
number  1995
1208
1209
1210
1211
number  3
1212
near "inganni": syntax error
1213
1214
1215
near "palmireni": syntax error
1216
1217
near "inganno": syntax error
1218
1219
1220
1221
1222
1223
1224
1225
1226
1227
1228
number  5
1229
1230
1231
number  4
1232
1233
1234
1235
1236
1237
1238
1239
1240
1

2354
2355
2356
2357
2358
number  1999
2359
2360
2361
2362
2363
2364
2365
2366
2367
2368
2369
2370
2371
2372
2373
number  400
2374
2375
2376
2377
2378
2379
2380
2381
2382
2383
2384
2385
2386
2387
number  2005
2388
2389
number  2008
2390
2391
2392
2393
2394
number  18
2395
2396
2397
2398
2399
2400
2401
number  2007
2402
number  2010
2403
2404
2405
2406
2407
number  10
2408
2409
2410
2411
2412
2413
number  2.7
2414
2415
2416
2417
2418
2419
2420
2421
number  2011
2422
2423
2424
2425
2426
2427
2428
2429
2430
2431
number  10
2432
2433
2434
2435
2436
2437
2438
2439
'NoneType' object has no attribute 'lower'
2440
2441
number  1
2442
2443
2444
2445
2446
2447
2448
2449
2450
2451
2452
2453
2454
2455
2456
2457
2458
2459
2460
2461
2462
2463
number  200
2464
2465
2466
number  400
2467
2468
number  1931
2469
2470
number  1922
2471
2472
2473
2474
2475
2476
2477
number  1000
number  1200
2478
number  1115
2479
2480
2481
number  -9
2482
number  1960
2483
2484
number  1967
2485
2486
number  1963
2487
num

3536
number  2002
3537
3538
number  2004
number  2009
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
number  2
3575
3576
3577
3578
3579
number  3
3580
3581
3582
number  1997
3583
3584
3585
3586
3587
number  2012
3588
3589
3590
3591
3592
3593
3594
3595
number  3
3596
number  3
3597
number  500
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
'NoneType' object has no attribute 'lower'
3609
3610
3611
'NoneType' object has no attribute 'lower'
3612
3613
3614
3615
3616
3617
3618
3619
number  4
3620
3621
3622
3623
3624
3625
3626
3627
3628
number  2010
number  2001
3629
3630
3631
3632
number  2004
number  2004
3633
3634
3635
number  2007
3636
3637
3638
3639
number  3
number  3
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
no such column: c3_list_number
no such column: c3_list_number
3651
number  1960
3652
3653
3654
3655
3656
3657
3658
3659
3660
36

4769
4770
4771
number  20
4772
4773
number  100
number  500
4774
4775
4776
4777
4778
4779
4780
4781
4782
4783
number  3
4784
number  5
4785
4786
number  1
4787
number  1
4788
4789
4790
4791
number  10
4792
4793
4794
4795
number  5
4796
4797
4798
4799
4800
4801
4802
4803
4804
4805
4806
4807
4808
4809
4810
4811
4812
4813
4814
4815
4816
4817
4818
4819
4820
4821
4822
4823
4824
4825
4826
4827
4828
number  0
4829
4830
4831
4832
4833
4834
4835
4836
4837
4838
4839
4840
4841
4842
4843
number  1970
4844
4845
4846
4847
4848
number  80
number  2008
4849
number  2008
number  165
4850
4851
4852
4853
number  10
4854
4855
4856
4857
4858
4859
4860
4861
4862
number  10
4863
4864
4865
4866
4867
4868
4869
4870
4871
4872
number  1
4873
4874
4875
4876
4877
4878
4879
4880
4881
4882
4883
4884
4885
number  1995
4886
4887
4888
4889
4890
4891
4892
4893
4894
number  100
4895
number  0.6
4896
number  9.5
4897
4898
4899
number  5
number  5000
4900
4901
4902
4903
number  2.2
4904
number  1973
4905
number  1941
4906


5991
5992
number  17
5993
5994
5995
5996
5997
5998
5999
6000
number  90
6001
number  60
6002
6003
number  1000
6004
number  90
6005
6006
6007
6008
6009
6010
6011
6012
6013
number  1944
6014
6015
6016
6017
6018
6019
6020
6021
6022
6023
6024
6025
6026
number  2004
6027
6028
6029
6030
6031
number  2002
6032
number  15
number  15
6033
near "c5_result": syntax error
6034
6035
6036
6037
number  4
6038
6039
6040
number  4
6041
6042
6043
6044
6045
6046
6047
6048
6049
6050
6051
6052
6053
number  5
6054
6055
number  1994
6056
6057
6058
6059
6060
6061
6062
6063
number  1990
6064
6065
6066
number  2006
6067
6068
number  1992
6069
6070
number  2003
6071
6072
number  2004
6073
number  1992
6074
6075
number  1997
6076
6077
6078
6079
number  6
6080
6081
6082
6083
6084
6085
number  4
6086
6087
6088
6089
6090
number  1962
6091
6092
6093
6094
number  1970
6095
6096
number  15
6097
number  10
6098
number  2009
6099
number  2007
6100
number  2012
6101
6102
number  2001
6103
number  400
6104
6105
6106
6107


7250
7251
7252
7253
7254
7255
number  2015
7256
'NoneType' object has no attribute 'lower'
7257
'NoneType' object has no attribute 'lower'
7258
'NoneType' object has no attribute 'lower'
7259
'NoneType' object has no attribute 'lower'
7260
7261
7262
'NoneType' object has no attribute 'lower'
7263
'NoneType' object has no attribute 'lower'
7264
7265
7266
number  30
7267
7268
7269
7270
7271
7272
7273
7274
7275
number  25
7276
7277
number  1988
7278
7279
number  1988
7280
near "hagan": syntax error
7281
7282
near "hagan": syntax error
7283
7284
7285
7286
7287
7288
7289
number  3
7290
7291
7292
7293
7294
7295
7296
7297
number  10
7298
7299
7300
7301
7302
7303
7304
7305
7306
7307
7308
7309
7310
7311
7312
7313
7314
7315
7316
7317
7318
7319
7320
no such column: c2_away
7321
number  59
7322
7323
no such column: c2_away
7324
7325
7326
number  2
7327
7328
number  20
7329
7330
7331
7332
7333
7334
7335
number  2500
7336
number  2000
7337
7338
7339
7340
7341
near "t": syntax error
7342
7343
number 

number  2008
8489
8490
8491
8492
number  2006
8493
8494
8495
number  2012
8496
8497
8498
8499
8500
8501
8502
number  2
8503
8504
8505
8506
number  3
8507
8508
8509
number  2000
8510
8511
8512
8513
8514
8515
8516
8517
8518
8519
8520
8521
8522
8523
8524
8525
8526
8527
8528
8529
8530
'NoneType' object has no attribute 'lower'
8531
8532
8533
8534
8535
number  1801
8536
8537
8538
number  1801
8539
number  1831
8540
8541
8542
8543
8544
8545
number  12
8546
8547
8548
8549
8550
number  2000
8551
number  2000
8552
8553
8554
number  2010
8555
8556
8557
8558
8559
8560
number  2007
8561
8562
8563
8564
8565
8566
8567
number  20
8568
8569
8570
8571
8572
8573
number  2002
8574
8575
number  5
8576
'NoneType' object has no attribute 'lower'
8577
8578
8579
'NoneType' object has no attribute 'lower'
number  2010
8580
8581
'NoneType' object has no attribute 'lower'
number  2000
8582
8583
8584
number  2
8585
8586
8587
8588
8589
8590
8591
8592
8593
8594
8595
8596
8597
8598
8599
8600
8601
8602
8603
number  1

number  3
9831
9832
9833
9834
9835
9836
9837
number  1970
9838
9839
9840
9841
9842
9843
9844
number  2000
number  2006
9845
9846
9847
9848
9849
9850
9851
9852
9853
9854
9855
9856
number  1964
9857
9858
9859
9860
number  1
number  2008
9861
9862
9863
9864
9865
9866
9867
9868
number  75
9869
9870
9871
9872
9873
9874
9875
9876
9877
9878
9879
number  25
9880
9881
9882
9883
9884
9885
9886
9887
9888
9889
9890
9891
number  50
9892
9893
9894
9895
9896
9897
near "bar": syntax error
9898
near "bar": syntax error
9899
9900
no such column: c15
9901
9902
9903
9904
9905
9906
9907
no such column: c7
9908
number  5
9909
9910
9911
9912
9913
9914
9915
9916
9917
9918
9919
number  3
9920
number  1
9921
number  3
9922
9923
9924
9925
9926
9927
9928
9929
9930
9931
9932
number  2
9933
9934
9935
9936
number  1996
9937
number  2002
9938
9939
number  2003
9940
9941
9942
number  1
9943
9944
9945
9946
number  5
9947
9948
9949
9950
9951
9952
9953
9954
9955
number  2
9956
9957
9958
9959
number  20
9960
9961
9962
996

10990
10991
number  1983
number  1984
10992
10993
10994
10995
10996
10997
10998
10999
11000
11001
11002
11003
11004
near "c5_result": syntax error
11005
11006
11007
11008
number  16
number  16
11009
11010
11011
11012
11013
11014
11015
11016
11017
number  1994
11018
number  2010
11019
11020
11021
number  1869
11022
11023
11024
11025
11026
11027
11028
11029
11030
11031
11032
11033
11034
11035
number  2008
11036
number  2012
11037
number  1966
11038
11039
number  1978
11040
11041
11042
number  2013
11043
number  1
11044
number  10
11045
11046
11047
11048
11049
11050
11051
11052
11053
11054
11055
'NoneType' object has no attribute 'lower'
11056
number  2000
11057
11058
11059
11060
11061
11062
number  20
11063
11064
11065
number  15
no such column: ret
11066
number  6
11067
11068
11069
11070
11071
number  10
11072
11073
11074
number  5
11075
11076
11077
11078
11079
number  1974
11080
11081
number  13
11082
11083
11084
11085
11086
11087
number  14
11088
11089
number  13.29
11090
11091
11092


In [115]:
entail = 0
contra = 0
for d in data:
    try:
        entail += len(d['entailments'])
        contra += len(d['contradictions'])
    except: pass

print(entail)
print(contra)

44469
72087


In [116]:
for d in data:
    print(d)
    break

{'nt': 'nt-2254', 'columns': [['constituency', ['constituency'], ['number'], 'number', '1'], ['region', ['region'], [], 'text', 'arica and parinacota\ntarapaca'], ['name', ['name'], ['first', 'second'], 'text(text)', 'jose antonio gomez urrutia\n(vice-president, march 11, 2010-march 15, 2011; march 20, 2013-present)'], ['party', ['party'], [], 'text', 'ps'], ['last elected', ['last', 'elected'], ['number'], 'number', '2009']], 'nl': ['what', 'is', 'the', 'difference', 'in', 'years', 'between', 'constiuency', '1', 'and', '2', '?'], 'nl_pos': ['WP', 'VBD-AUX', 'DT', 'NN', 'IN', 'NNS', 'IN', 'NN', 'CD', 'CC', 'CD', '.'], 'nl_ner': ['O', 'O', 'O', 'O', 'O', 'DURATION', 'O', 'O', 'NUMBER', 'O', 'NUMBER', 'O'], 'nl_ralign': [['None', None], ['None', None], ['None', None], ['Keyword', ['diff', '']], ['None', None], ['Column', 'c5_number'], ['Keyword', ['diff', '']], ['Column', 'c1_number'], ['Literal', None], ['Keyword', ['diff', '']], ['Literal', None], ['None', None]], 'nl_typebio': ['O', '

In [117]:
import json
x = open('squall_augmented_20_june.json','w')
st = json.dumps(data)
x.write(st)

30536210

In [79]:
import copy
import unidecode

all_count = 0

for d in data:
    all_found = True
    skeleton = unidecode.unidecode(d['converted_statement'])
    output_string = unidecode.unidecode(str(d['tgt']))
    skeleton_update = skeleton.lower().replace(" " + output_string.lower() + " ", " tgt ").replace(output_string.lower() + " ", "tgt ").replace(" " + output_string.lower(), " tgt")
    if skeleton_update == skeleton : all_found = False
    skeleton = skeleton_update
    
    d['skeleton_sql'] = copy.deepcopy(d['sql'])
    value_count = 1
    for al in d['align']:
        if len(al[1]) == 1 and d['sql'][al[1][0]][0] == "Column": 
            al[0].sort(key=int)
            nl = " ".join(str(d['nl'][x]) for x in al[0])
            skeleton_update = skeleton.replace(str(nl), str(d['sql'][al[1][0]][1]))
            if skeleton_update == skeleton : all_found = False
            skeleton = skeleton_update
        if len(al[1]) == 1 and d['sql'][al[1][0]][0] == "Literal.String": 
            al[0].sort(key=int)
            nl = " ".join(str(d['nl'][x]) for x in al[0])
            col_n = ""
            for i in range(0, al[1][0]):
                if d['sql'][al[1][0]-i][0] == "Column":
                    col_n = d['sql'][al[1][0]-i][1]
                    break
            skeleton_update = skeleton.lower().replace(str(nl).lower(), (str(col_n) + "_string_value_" + str(value_count)).lower())
            d['skeleton_sql'][al[1][0]][1] = str(col_n) + "_string_value_" + str(value_count)
            if skeleton_update == skeleton : all_found = False
            skeleton = skeleton_update
            value_count += 1
        if len(al[1]) == 1 and d['sql'][al[1][0]][0] == "Literal.Number": 
            al[0].sort(key=int)
            nl = " ".join(str(d['nl'][x]) for x in al[0])
            col_n = ""
            for i in range(1, al[1][0]):
                if d['sql'][al[1][0]-i][0] == "Column":
                    col_n = d['sql'][al[1][0]-i][1]
                    break
            skeleton_update = skeleton.replace(str(nl).lower(), (str(col_n) + "_number_value_" + str(value_count)).lower())
            if skeleton_update == skeleton : all_found = False
            skeleton = skeleton_update
            d['skeleton_sql'][al[1][0]][1] = str(col_n) + "_number_value_" + str(value_count)
            value_count += 1
#     print(d['converted_statement'])
#     print(" ".join(str(x[1]) for x in d['sql']))
#     print(" ".join(str(x[1]) for x in d['skeleton_sql']))
    
#     print(str(d['tgt']))
    
    if all_found: 
        print(d['title'])
        skeleton = skeleton.lower().replace(d['title'].lower(),"table_title")
        d['skeleton_statement'] = skeleton
        print(d['converted_statement'])
        print(" ".join(str(x[1]) for x in d['sql']))
        print(" ".join(str(x[1]) for x in d['skeleton_sql']))
        print(str(d['tgt']))
        print(skeleton)
        all_count += 1
        print("\n\n")

Senate of Chile
The total number of constituencies is 19.
select count ( distinct c1 ) from w
select count ( distinct c1 ) from w
19
the total number of c1 is tgt.



Senate of Chile
Jaime Quintana belonged to the PPD party.
select c4 from w where c3 = 'jaime quintana'
select c4 from w where c3 = c3_string_value_1
PPD
c3_string_value_1 belonged to the tgt c4.



Senate of Chile
The last region listed on the table is Magallanes.
select c2 from w order by id desc limit 1
select c2 from w order by id desc limit 1
Magallanes
the last c2 listed on the table is tgt.



Senate of Chile
Fulvio Rossi is the first name on the table.
select c3 from w where id = 1
select c3 from w where id = 1
Fulvio Rossi
tgt is the first c3 on the table.



List of North American tornadoes and tornado outbreaks
4 tornadoes occurred in 1965.
select count ( * ) from w where c2_minimum_year = 1965
select count ( * ) from w where c2_minimum_year = c2_minimum_year_number_value_1
4
tgt tornadoes occurred c2_minimum_ye

Coventry Council election, 2007
The number of staying councillors that the labor party had was 13.
select c3_number from w where c1 = 'labour'
select c3_number from w where c1 = c1_string_value_1
13
the number of c3_number that the c1_string_value_1 c1 had was tgt.



Coventry Council election, 2007
4 parties had zero councils.
select count ( c1 ) from w where c6_number = 0
select count ( c1 ) from w where c6_number = 0
4
tgt c1 had zero c6_number.



2008 ARCA Re/Max Series season
Racing For Wildlife 200 was after the race in pocono.
select c3 from w where c2_parsed > ( select c2_parsed from w where c4 = 'pocono' ) order by c2_parsed asc limit 1
select c3 from w where c2_parsed > ( select c2_parsed from w where c4 = c4_string_value_1 ) order by c2_parsed asc limit 1
Racing For Wildlife 200
tgt was after the c3 c4 c4_strc4g_value_1.



2008 ARCA Re/Max Series season
The total number of races in this series is 21.
select count ( c3 ) from w
select count ( c3 ) from w
21
the total number

List of flag bearers for Samoa at the Olympics
6 different people have born the glad for samoa at the olympics.
select count ( distinct c4 ) from w
select count ( distinct c4 ) from w
6
tgt different c4 have born the glad for samoa at the olympics.



List of flag bearers for Samoa at the Olympics
7 years were held in summer.
select count ( c2 ) from w where c3 = 'summer'
select count ( c2 ) from w where c3 = c3_string_value_1
7
tgt c2 were held in c3_string_value_1.



List of flag bearers for Samoa at the Olympics
Samoa has been represented at the summer olympics 7 times.
select count ( * ) from w where c3 = 'summer'
select count ( * ) from w where c3 = c3_string_value_1
7
samoa has been represented at the c3_string_value_1 olympics tgt times.



List of flag bearers for Samoa at the Olympics
Ele opeloge was the samoa flag bearer at the olympics for 2 years.
select count ( c2 ) from w where c4 = 'ele opeloge'
select count ( c2 ) from w where c4 = c4_string_value_1
2
c4_string_value_1

Vavuniya represented 11 camps.
select count ( c1 ) from w where c2 = 'vavuniya'
select count ( c1 ) from w where c2 = c2_string_value_1
11
c2_string_value_1 represented tgt c1.



Sri Lankan IDP numbers, February and March 2009
Vengalachedikulam was the first div sec division.
select c2 from w where id = 1
select c2 from w where id = 1
Vengalachedikulam
tgt was the first c2.



The Citadel Bulldogs baseball
The number of loses while Fred Jordan was coaching was 552.
select c5_number from w where c1 = 'fred jordan'
select c5_number from w where c1 = c1_string_value_1
552
the number of c5_number while c1_string_value_1 was c1 was tgt.



The Citadel Bulldogs baseball
Chal Port is the only coach with 2 ties on their record.
select c1 from w where c6_number = 2
select c1 from w where c6_number = c6_number_number_value_1
Chal Port
tgt is the only c1 with c6_number_number_value_1 c6_number on their record.



The Citadel Bulldogs baseball
2 coaches had above 500 wins.
select count ( c1 ) fro

Iryna Shpylova was the top ranked competitor in this race.
select c2 from w where c1_number = 1
select c2 from w where c1_number = 1
Iryna Shpylova
tgt was the top c1_number c2 in this race.



2009–10 UCI Track Cycling World Cup Classics – Round 2 – Women's scratch race
The number rank of Belgium is 2.
select c1_number from w where c3 = 'belgium'
select c1_number from w where c3 = c3_string_value_1
2
the number c1_number of c3_string_value_1 is tgt.



2009–10 UCI Track Cycling World Cup Classics – Round 2 – Women's scratch race
2 cyclists do not have -1 laps down.
select count ( c2 ) from w where c4 is null
select count ( c2 ) from w where c4 is null
2
tgt c2s do not have -1 c4.



2009–10 UCI Track Cycling World Cup Classics – Round 2 – Women's scratch race
Yekatsiryna Barazna is the last cyclist listed.
select c2 from w order by id desc limit 1
select c2 from w order by id desc limit 1
Yekatsiryna Barazna
tgt is the last c2 listed.



Seaton Tramway
The number of operational vehicl

...




1961–62 Segunda División
The total number of points scored by the first place team is 40.
select c4 from w where c1_number = 1
select c4 from w where c1_number = c1_number_number_value_1
40
the total number of c4 scored by the c1_number_number_value_1 c1_number team is tgt.



1961–62 Segunda División
CD Villarrobledo is the only team that had more than 21 losses.
select c2 from w where c7_number > 21
select c2 from w where c7_number > c7_number_number_value_1
CD Villarrobledo
tgt is the only c2 that had more than c7_number_number_value_1 c7_number.



Vålerenga Fotball
The name of the first competition listed is Inter-Cities Fairs Cup.
select c2 from w where id = 1
select c2 from w where id = 1
Inter-Cities Fairs Cup
the name of the first c2 listed is tgt.



Vålerenga Fotball
The competition that occurred directly after the European Cup in 1985-86 was the UEFA Cup.
select c2 from w where c1 > ( select c1 from w where c2 = 'european cup' and c1 = '1985-86' ) order by c1 asc limit 1


Kang Ji-hwan
The total number of awards that this actor has won is 15.
select count ( c2 ) from w where c5 = 'won'
select count ( c2 ) from w where c5 = 'won'
15
the total number of c2 that this actor has won is tgt.



1988 West Coast Eagles season
8 rounds had more than 20,000 spectators in attendance.
select count ( * ) from w where c8_number > 20000
select count ( * ) from w where c8_number > c8_number_number_value_1
8
tgt rounds had more than c8_number_number_value_1 spectators in c8_number.



1988 West Coast Eagles season
The date of the last win was 28 August.
select c2 from w where c3_second_number > c5_second_number order by c2_parsed desc limit 1
select c2 from w where c3_second_number > c5_second_number order by c2_parsed desc limit 1
28 August
the c2 of the last win was tgt.



1988 West Coast Eagles season
Subiaco Oval was the first venue to have over 30,000 attendees.
select c7 from w where c8_number > 30000 order by c2_parsed asc limit 1
select c7 from w where c8_numbe

2
tgt games were played c3_raw c3_raw_string_value_1.



2013–14 Chicago State Cougars women's basketball team
The total attendance at the wright state and loyola games was 551.
select sum ( c7_number ) from w where c3_raw in ( 'wright state' , 'loyola' )
select sum ( c7_number ) from w where c3_raw in ( c3_raw_string_value_1 , c3_raw_string_value_2 )
551
the total c7_number at the c3_raw_string_value_1 and c3_raw_string_value_2 games was tgt.



2013–14 Chicago State Cougars women's basketball team
29 games were played in the regular season.
select count ( c2 ) from w
select count ( c2 ) from w
29
tgt games were played in the regular season.



List of Syrian Air Force bases
The first airbase listed on the chart is Abu al-Duhur Military Airbase.
select c1 from w where id = 1
select c1 from w where id = 1
Abu al-Duhur Military Airbase
the first c1 listed on the chart is tgt.



List of Syrian Air Force bases
The total number of helipads at hama military airport is 10.
select c5_number 

September 10, 1995
the c2 for the first game c5 c5_string_value_1 is tgt.



Aachen Cathedral
The diameter of the smallest bell is 793.
select min ( c5_number ) from w
select min ( c5_number ) from w
793
the c5_number of the smallest bell is tgt.



Aachen Cathedral
Maria is the name of the heaviest bell.
select c2 from w order by c4_number desc limit 1
select c2 from w order by c4_number desc limit 1
Maria
tgt is the c2 of the c4_number bell.



Aachen Cathedral
Maria is the name of the bell with the most diameter.
select c2 from w order by c5_number desc limit 1
select c2 from w order by c5_number desc limit 1
Maria
tgt is the c2 of the bell with the most c5_number.



Aachen Cathedral
The name of the bell with the weight of only 425 kg is Petrus.
select c2 from w where c4_number = 425
select c2 from w where c4_number = c4_number_number_value_1
Petrus
the c2 of the bell with the c4_number of only c4_number_number_value_1 kg is tgt.



MTV Indonesia Movie Awards
The first category lis

tgt were played on a c4_string_value_1 c4.



Jane O'Donoghue
Jane O'Donoghue has competed in 11 tournaments.
select count ( c3 ) from w
select count ( c3 ) from w
11
table_title has competed in tgt c3.



Philadelphia Phillies all-time roster (D)
There are 12 left fielders on the list.
select count ( * ) from w where c3 = 'left fielder'
select count ( * ) from w where c3 = c3_string_value_1
12
there are tgt c3_string_value_1 on the list.



Philadelphia Phillies all-time roster (D)
The last position on the chart is center fielder.
select c3 from w order by id desc limit 1
select c3 from w order by id desc limit 1
Center fielder
the last c3 on the chart is tgt.



Carlo Corazzin
4 games in los angeles.
select count ( * ) from w where c3 = 'los angeles'
select count ( * ) from w where c3 = c3_string_value_1
4
tgt games c3 c3_strc3g_value_1.



Carlo Corazzin
The last venue before the opponent Colombia was Qualcomm Stadium, San Diego, United States.
select c3 from w where c2_parsed < ( s

In [101]:
for d in data:
    print(d)
    break

{'nt': 'nt-2254', 'columns': [['constituency', ['constituency'], ['number'], 'number', '1'], ['region', ['region'], [], 'text', 'arica and parinacota\ntarapaca'], ['name', ['name'], ['first', 'second'], 'text(text)', 'jose antonio gomez urrutia\n(vice-president, march 11, 2010-march 15, 2011; march 20, 2013-present)'], ['party', ['party'], [], 'text', 'ps'], ['last elected', ['last', 'elected'], ['number'], 'number', '2009']], 'nl': ['what', 'is', 'the', 'difference', 'in', 'years', 'between', 'constiuency', '1', 'and', '2', '?'], 'nl_pos': ['WP', 'VBD-AUX', 'DT', 'NN', 'IN', 'NNS', 'IN', 'NN', 'CD', 'CC', 'CD', '.'], 'nl_ner': ['O', 'O', 'O', 'O', 'O', 'DURATION', 'O', 'O', 'NUMBER', 'O', 'NUMBER', 'O'], 'nl_ralign': [['None', None], ['None', None], ['None', None], ['Keyword', ['diff', '']], ['None', None], ['Column', 'c5_number'], ['Keyword', ['diff', '']], ['Column', 'c1_number'], ['Literal', None], ['Keyword', ['diff', '']], ['Literal', None], ['None', None]], 'nl_typebio': ['O', '

In [80]:
all_count

5374

In [81]:
import nltk
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/aashnajena/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/aashnajena/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/aashnajena/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [82]:
f = open('word_freq_final','r')
freq = json.load(f)

In [83]:
print(freq.keys())

dict_keys(['game', 'medal', 'team', 'season', 'scored', 'released', 'win', 'he', 'race', 'earned', 'received', 'one', 'point', 'place', 'people', 'his', 'album', 'competed', 'she', 'me', 'competition', 'round', 'player', 'score', 'goal', 'award', 'song', 'event', 'produced', 'office', 'appeared', 'actor', 'two', 'car', 'participated', 'her', 'olympics', '-lrb-', '-rrb-', 'term', 'country', 'awarded', 'built', 'achieved', 'episode', 'nation', 'recorded', 'play', 'station', 'football', 'club', 'league', 'lost', 'day', 'championship', 'c2s', 'home', 'track', 'television', 'state', 'drafted', 'picked', 'city', 'nominated', 'c4s', 'career', 'runner', 'film', 'you', 'meter', 'tournament', '2009', 'series', 'victory', 'competitor', '2002', 'starred', '10', 'draft', 'election', 'ran', 'vote', 'olympic', 'member', 'group', 'winning', 'men', 'world', '2012', 'run', 'featured', 'cup', 'performed', 'part', 'qualified', 'vehicle', 'athlete', 'driver', 'c1s', 'woman', 'movie', 'directed', 'zero', 'w

In [84]:
words = {}
import nltk
from nltk import word_tokenize
from nltk.stem import WordNetLemmatizer 
lemmatizer = WordNetLemmatizer()

In [85]:
skeletons = []
for d in data:
    if "skeleton_statement" in d.keys():
        good = True
        for key in freq.keys():
            if key.lower() in [lemmatizer.lemmatize(i) for i in nltk.word_tokenize(d['skeleton_statement'].lower())]: 
                good = False
        if good: 
            print(d['skeleton_statement'])
            skeletons.append([d['skeleton_statement'], d['skeleton_sql']])

the total number of c1 is tgt.
the last c2 listed on the table is tgt.
tgt is the first c3 on the table.
tgt c2 were either c5_string_value_1 or c5_string_value_2.
tgt c2 are from c2_second_string_value_1.
tgt c1 were listed as c3_string_value_1.
tgt c1 have an c4_number above c4_number_number_value_1.
the c2_number was above c2_number_number_value_1 for tgt c1.
the number of c1 c5_year after c5_year_number_value_1 is tgt.
the only c1 to be less than c2_second_number_number_value_1 c2_second_number is tgt.
the combined c2_second_number of c1_string_value_1 and c1_string_value_2 is tgt.
the total c4 of c1_string_value_1 is tgt.
the c8 c1_number c1_number_number_value_1 was tgt.
there are tgt c2 in total.
c8_string_value_1 was the c8 tgt times.
c4_string_value_1 was the c4 tgt times.
the name of the first c9 according to this chart was tgt.
tgt c2 had over $ c5_number_number_value_1 c5_number.
tgt c7_number from c1_number_number_value_1 to c1_number_number_value_2.
the last c1_number the

they had tgt c2 the previous c1_number of c1_number_number_value_1.
table_title's only c2 c1_number c1_number_number_value_1 was tgt.
the total number of c5_string_value_1 c5 listed in the table is tgt.
the least amount of c7_number completed is tgt.
there were tgt total c6_string_value_1 c6.
tgt c1 are listed.
c7_number1 for c4 c4_string_value_1 is tgt.
there are at least c2_number_value_1 c2 on this list.
tgt c1 c2 from c2_string_value_1.
the last c3 on the chart is tgt.
the last c3 is tgt.
the number of c2 for c3_string_value_1 is tgt.
tgt c2 have c1_first_string_value_1 as a c1_first.
tgt is the only c2 c3 of c3_string_value_1.
tgt is the c5 where the c1 is c1_string_value_1 and the c4 is c4_string_value_2.
the number of times c1_string_value_1 is listed as the c1 is tgt.
the top c5_number listed is tgt.
tgt was a c1 that had c4_number higher than c4_number_number_value_2 but a c6_number lower than c6_number_number_value_1.
the total number of c5 c1_number c1_number_strc1_numberg_v

there are tgt c4 in total.
tgt is the only c2 under c5_min_number_value_1 c5_min.
the c5 c2 is tgt.
there were tgt total c2 between c1_minimum_year_number_value_1 and c1_maximum_year_number_value_2.
the total number of c2 is tgt.
c2_string_value_1 served tgt years.
the c2 for c5_string_value_1 is tgt.
a c4_string_value_1 is tgtt the same as a c4_string_value_2.
the c2 of the c1_number_number_value_1 c1_number was tgt.
there are tgt c1 total.
the total number of c1 c4 c4_string_value_1 is tgt.
tgt of the c1 were c3_month c3_month_number_value_1.
the only c1 with c6_number_number_value_1 % c6_number are tgt.
tgt is the c1 that has the longest c8_number.
tgt is the only c1 to have a negative c3 average.
c1_string_value_1 and c1_string_value_2 had tgt c5_number altogether.
the only c2 c3 c3_string_value_1 was the tgt.
the number of c2 c1_maximum_month c1_maximum_month_number_value_1 were tgt.
there are tgt c2 total on the chart.
the number of c1 covered in the table is tgt.
the number of t

the number of c7 for the c3_raw_string_value_1 is tgt.
in the chart, c4_string_value_1 is before c4_string_value_2.
c5_string_value_2 is tgtt at least on the chart c5_number_value_1 times.
the c5_string_value_2 is on the chart tgt than c5_number_value_1 times.
c5_string_value_1 is listed tgt times as the c5.
tgt c2 c5_month c5_month_number_value_1.
the only c2 to c6_month c6_month_number_value_1 was the tgt.
the difference in years from _number_value_1 to _number_value_2 was tgt.
the largest c1 is tgt.
tgt was the first c2 to be c3_number.
the total number of c1 who are c2_string_value_1 is tgt.
the total amount of current c1 who are c2_string_value_1 is tgt.
tgt c1 had c2_string_value_1 listed as their c2.
tgt of the current c1 have a listed c5.
tgt of the current c1 will be c4_number at least c4_number_number_value_1.
tgt c7_string_value_1 c7 are listed.
tgt are the c4 which are under the c7_string_value_1 c7.
the total amount of a c4_number c1_string_value_1 is tgt.
a c3_number c1_s

tgt c2 were made in c1_number_number_value_1.
the c5 for c1_number c1_number_number_value_1 was tgt.
tgt was the c3_raw for c1_number c1_number_number_value_1.
there were tgt c4_number c1_number c1_number_number_value_1.
there was tgt c6 c1_number c1_number_number_value_1.
the c2_number c1_number c1_number_number_value_1 was tgt %.
tgt was the c1_number with the most c2_number.
there are tgt total c3_string_value_1 c3 c1.
the number of c1 c2_number in c2_number_number_value_1 is tgt.
tgt c1 are listed on the chart total.
the last c2 on the chart is tgt.
tgt is the only c3 from c5_string_value_1.
tgt c1 have at least c5_number_number_value_1 listed for c5_number.
tgt c1 were c3_number before c3_number_number_value_1.
c1_string_value_1 is c2 tgt.
the number of titles in which the c5 played on was c5_string_value_1 is tgt.
other than c2_string_value_1, they also c4_first_numberd c4_first_number_number_value_2 in tgt.
tgt c1 were c6_year before c6_year_number_value_1.
the first c2 c6_parse

...

tgt c4_first_number and c5_first_number for c1_string_value_1.
tgt c1 were represented in the c3.
the c2 on c1_string_value_1 was tgt.
tgt were the top c8_number_number_value_1 cc8_number_number_value_1 in the table_title.
c3_string_value_1 completed tgt c5_number in the table_title.
c1_string_value_1 is listed tgt the c1_string_value_2.
the number of c1 with c4_string_value_1 c4 is tgt.
the last c1 c3_second c3_second_string_value_1 is tgt.
tgt is the first c1 c3_first c3_first_string_value_1.
the total c4 for the c1_string_value_1 in c2_string_value_2 is tgt.
the name of the first c3 is tgt.
the first c1 listed as c3_string_value_1 is tgt.
tgt c3_string_value_1 c2 were c5_string_value_2 after c1_year_number_value_3.
tgt c2 have a c4_number above c4_number_number_value_1.
tgt c2 were c5_string_value_1.
there are tgt c1 on the table.
the total c4_number of c2_string_value_1h is tgt.
tgt c2 have a c3_number above c3_number_number_value_1.
the first c2 used c1_mc1_minimum_monthimum_year 

tgt c2 were made under the c5 of c5_string_value_1.
tgt c2 have an c6_number over c6_number_number_value_1.
c6_string_value_1's c2 was tgt.
tgt is the only c2 with no c4.
the number of c5 on the chart is tgt.
the c3 c3_string_value_1 was used tgt times.
tgt were c7_string_value_1 c7.
the c7 was listed as c7_string_value_1 tgt times.
the total number of c2 held c2_month c2_month_number_value_1 is tgt.
the name of the last c3 on this chart is tgt.
the total amount of c8_number between the c1_number_number_value_1 and c1_number_number_value_2 c1_number is tgt.
the c2 tgt had the least c8_number.
the c4 for each c2 is tgt.
tgt c1 had no c4 results.
the number of c1 with a c5_number over c5_number_number_value_1 is tgt.
tgt c1 are not c6_string_value_1s.
c3_string_value_1 is listed tgt times on this chart.
tgt has c4_number c4_number_number_value_1.
tgt is the c1 listed last on this chart.
there are tgt c1_number_value_1 c1.
there are tgt c4 in total.
the c5 was  c5_string_value_1 '' tgt ti

the total number of c6 listed is tgt.
the last c3 listed is tgt.
tgt c2 have at least c4_number_number_value_1 c4_number.
tgt is the first c2 according to this chart.
the total number of c2 is tgt.
the number of times c5_string_value_1 is listed as the c5 on this chart is tgt.
the c3_raw was the c3_raw_string_value_1 tgt times.
tgt was the c7 in c1_number c1_number_number_value_1.
the total number of c1 is tgt.
c7_string_value_1 has been the c7 tgt times.
c5_string_value_1 has held the c5 tgt times.
tgt c2 had c8_string_value_1 as c8.
tgt c7 in c1_number c1_number_number_value_1.
tgt different c2 have c3_number.
the total number of c6_number between c2_string_value_1, c2_string_value_2, c2_string_value_3, and c2_string_value_4 is tgt.
tgt were in the first c1_string_value_1 match.
tgt shows were c6_string_value_1.
the longest c2 is the tgt.
the total number of c6 listed is tgt.
c4_string_value_1 appears tgt tic4_string_value_1es under the c4 coluc4_string_value_1n.
the total number of 

tgt is the c5 with the highest number of c6_number.
the first c1 listed on this chart is tgt.
tgt c1 are listed on this chart.
tgt is the only c2 on the list that is c5 c5_strc5g_value_1.
tgt c2 are above c3_number_number_value_1 c3_number.
tgt c2 are c4 c4_string_value_1.
the total c5 on c1_number c1_number_number_value_1 is tgt.
the total of c1_string_value_1 is tgt.
the only c5_string_value_1 c4 is in tgt
tgt c1 were c4_number before c4_number_number_value_1.
tgt c1 had c3_string_value_1 as their c3.
tgt is the only c1 to have c5.
tgt c2 c3 c3_string_value_1.
the total number of c3_string_value_1 c2 is tgt.
c3_string_value_1 had tgt c2 finish in the top c3_number_value_2.
tgt c2 from c3_string_value_1 ranked in the top c3_number_value_2.
c3_number number at least c3_number_number_value_1 for tgt c1.
the c4_number was at least c4_number_number_value_1 or more tgt times.
tgt c1 showed a positive c5_number.
tgt c1 of statistics are listed in chart.
tgt is the only c3 c5 c5_string_value

tgt has a c3_first_number of c3_first_number_number_value_1 but are only c5_string_value_2 c5.
the last c1 on this chart is tgt.
tgt c1 have a c4_first_number of at least c4_first_number_number_value_1.
the tgt c3 had c4_string_value_1 c4 and was used c2 c2_string_value_2.
tgt had at least c6_number_number_value_1 c6_number.
the total number of c1 listed is tgt.
there are tgt c1 c3 c3_string_value_1.
the c1 with the least c5_number listed here is tgt.
the total number of tallest c1 c3 c3_string_value_1 is tgt.
tgt different c3 served between c2_number_number_value_1 and c1_number_number_value_2.
the total of c2 is tgt.
the first c2 to c4_number was tgt.
tgt c2 were c5_number c5_number_number_value_1.
the total number of c4 is tgt.
c1_string_value_1 served for tgt years.
the total c1_number of c8 in c1_number_number_value_1 is tgt.
there are tgt c1 on the chart.
tgt c2 were c3 c3_string_value_1.
tgt c1 have a c3_number above c3_number_number_value_1.
tgt were played on a c4_string_value

In [86]:
len(skeletons)

2490

In [87]:
import json

e = open('skeletons.json','w')
st = json.dumps(skeletons)
e.write(st)

812188

In [119]:
p = open('skeletons.json','r')
skeletons = json.load(p)

In [120]:
trimmed = [s for s in skeletons if "table_title" not in s[0]]

In [121]:
print(len(trimmed), len(skeletons))


2406 2490


In [134]:
for d in data:
    d['extra_entailments'] = []
    d['extra_contradictions'] = []
    
    sampled = random.sample(trimmed, 8)
    con = sqlite3.connect('./tables/db/' + d['tbl'] + '.db')
    cursor = con.cursor()
    cursor.execute("select * from w")
    col_names = [i[0] for i in d['columns']]
    cols = {"string" : []}
    for i in cursor.description:
        if "_" not in i[0] and i[0] != "id" and i[0] != "agg": cols["string"].append(i[0])
        else:
            key = "_".join(i[0].split("_")[1:])
            if key in cols.keys(): cols[key].append(i[0])
            else: cols[key] = [i[0]]
    
    for sample in sampled:
        try:
            sql = sample[1]
            query = ""
            stmt = nltk.word_tokenize(sample[0].lower())
            dic = {}
            contra_values = []
            for token in sql:
                if token[1] in dic.keys() : query += dic[token[1]] + " "
                elif token[0] == "Column":
                    replace = ""
                    if "_" not in token[1] and token[1] != "id" and token[1] != "agg" and len(cols["string"]) > 0: 
                        replace = random.choice(cols["string"])
#                         print(replace)
                        col_index = int(replace.replace("c",""))
#                         print(col_index)
                        replace_col = col_names[col_index-1]
                        for i in range(0,len(stmt)): 
                            if stmt[i] == token[1]: stmt[i] = replace_col
                        dic[token[1]] = replace
                    else:
                        key = "_".join(token[1].split("_")[1:])
                        if key in cols.keys(): 
                            replace = random.choice(cols[key])
                            col_index = int(replace.split("_")[0].replace("c",""))
#                             print(col_index)
                            replace_col = col_names[col_index-1]
                            for i in range(0,len(stmt)): 
                                if stmt[i] == token[1]: stmt[i] = replace_col
                            dic[token[1]] = replace
                    query += replace + " "
                elif token[0] == "Literal.String":
                    key = dic[token[1].split("_string_value")[0]]
                    cursor.execute("select " + str(key) + " from w")
                    value = random.choice(cursor.fetchall())[0]
                    for i in range(0,len(stmt)): 
                        if stmt[i] == token[1]: stmt[i] = str(value)
                    dic[token[1]] = value
                    query += '"' + value + '" '
                    contra_value = value
                    for yy in range(5):
                        cursor.execute("select " + str(key) + " from w")
                        if contra_value == value : contra_value = random.choice(cursor.fetchall())[0]
#                     print(value, contra_value)
                    if contra_value != value and [value, contra_value] not in contra_values: contra_values.append([value, contra_value])
                elif token[0] == "Literal.Number":
                    key = dic[token[1].split("_number_value")[0]]
                    cursor.execute("select " + str(key) + " from w")
                    value = random.choice(cursor.fetchall())[0]
                    for i in range(0,len(stmt)): 
                        if stmt[i] == token[1]: stmt[i] = str(value)
                    dic[token[1]] = value
                    if value.is_integer() : value = int(value)
                    query += str(value) + " "
                    contra_value = value
                    for yy in range(5):
                        cursor.execute("select " + str(key) + " from w")
                        if contra_value == value : contra_value = random.choice(cursor.fetchall())[0]
#                     print(value, contra_value)
                    if contra_value != value and [value, contra_value] not in contra_values: contra_values.append([value, contra_value])
                else: query += str(token[1]) + " "

            cursor.execute(query)
            target = cursor.fetchall()
            if len(target)>0:
                if target[0][0] not in ['None','','-','N/A','n/a','TBD','—']:
                    for i in range(0,len(stmt)): 
                        if stmt[i] == "tgt": stmt[i] = str(target[0][0]).replace("\n","")
                    created_sent = " ".join(stmt)
                    if "None" not in created_sent and "tgt" not in created_sent and "c1" not in created_sent and "c2" not in created_sent and "c3" not in created_sent and "c4" not in created_sent and "c5" not in created_sent and "c6" not in created_sent:
                        d['extra_entailments'].append(created_sent.replace(".0 "," "))
                        cont_len = min(5,len(contra_values))
    #                     print(contra_values)
                        for x in range(0,cont_len):
                            refute = created_sent.replace(contra_values[x][0], contra_values[x][1])
                            if refute != created_sent and "None" not in refute: d['extra_contradictions'].append(refute.replace(".0 "," "))
                    
        except: pass


In [135]:
for d in data:
    print(d['extra_entailments'])
    print("contra ", d['extra_contradictions'])

['the total number of party on the chart is 38 .', '5 party are ps .', '4 last elected are santiago .', 'the last constituency on this chart is 19 .', 'ps had 2009 last elected .']
contra  ['5 party are pdc .', '4 last elected are maule .', 'pdc had 2009 last elected .']
["9 has won 2 constituency 's .", '19 different constituency are involved .', 'valparaiso had 2009 last elected .', '5 total ps party were won by ps .', 'the number of name made by hosain sabag castillo is 0 .', 'ps and ps have combined 49 constituency .', 'the number of region in this category that name pedro munoz aburto during this year is 1 .']
contra  ["13 has won 2 constituency 's .", 'santiago had 2009 last elected .', '5 total rn party were won by rn .', '5 total udi party were won by udi .', 'the number of name made by eduardo frei ruiz-tagle is 0 .', 'mas and mas have combined 49 constituency .', 'prsd and prsd have combined 49 constituency .', 'the number of region in this category that name hosain sabag cas

contra  ['1 attendance are an assembly hall • champaign, il .', 'the rank# of the 15148 and 13980 attendance combined is $ 488,761 .', 'the rank# of the 13106 and 16349 attendance combined is $ 488,761 .']
[]
contra  []
['the total of 2006-present is 2 .', 'ford taurus was in make for 1 notes .', '0 in service have no in service .', 'at least 3 notes have won .', 'the name of the last notes is retired .', 'ford freestar ride vehicle comes before chrysler pt cruiser community/education vehicle .', 'the total of make is 14 .']
contra  ['the total of 2002-present is 2 .', 'jeep cherokee was in make for 1 notes .', 'ford freestar ride vehicle comes before ford expedition .']
['the total number of different coordinates in the table is 12 .', 'the last coordinates listed in the table is 51°12′45′′n 113°39′3′′w\ufeff / \ufeff51.21250°n 113.65083°w .', 'there have been 1 28 county .', 'the finishing notes after the north to madden\nsouth to sage hill & evanston notes was north to maddensouth t

['the name of the pick # at the top of the chart is 25 .', 'memphis was 27 pick # .', 'the top pick # college is saskatchewan .', 'montreal alouettes won charleston southern college .', '26 was listed as a pick # 1 times .', 'there are 8 college .', '6 college pick # in under 31 seconds .', 'saskatchewan college has only 32 pick # .']
contra  ['simon fraser was 27 pick # .', 'calgary stampeders won charleston southern college .', '27 was listed as a pick # 1 times .']
['ol position has the most pick # .', 'there were 8 college .', '25 is the last pick # for pick # .', '32 is the pick # with the most pick # .', '7 of the locomotives were pick # before 32 .', 'wr/qb has a player of steven maheu .', 'the name of the next pick # after 27 is 28 .', 'the only position montreal alouettes cfl team is ot .']
contra  ['wr/qb has a player of kelly bates .', 'the name of the next pick # after 29 is 28 .', 'the only position calgary stampeders cfl team is ot .']
['4 pick # pick # before 29 .', 'the

['1 notes are listed .', 'there are 1 1 .', '3 time were played .', '8 rank are listed .', 'q is listed under the notes column of the last rank .']
contra  ['there are 4 4 .']
['1 q notes are listed .', 'the number of rank covered in the table is 8 .', '0 time are above 4 rank .', '1 rank had 5 rank .', '3 name were played .']
contra  []
['5 rank are in the top 5 rank .', '1 of the notes are rank 7 .', '2 time had an rank over 2 .', '7 notes made it into the top 7 rank .', '5 of the current rank will be rank at least 4 .']
contra  ['1 of the notes are rank 8 .']
['the total rank of 5 `` and 4 `` is 9 .', 'the total number of united states on the list is 2 .', 'united states was the nationality 2 times .']
contra  ['the total rank of 1 `` and 4 `` is 9 .', 'the total rank of 5 `` and 1 `` is 9 .']
['there are 8 rank on the chart .', '8 rank were played .', 'the total of the first 3 rank is 6 .']
contra  []
['4 was the rank 1 times .', '1 name are name julia stowers .', 'the total of nat

contra  []
['the name of the last silver on this chart is 0 .', 'the last gold on the list is 0 .', '1 gold were silver 5 .', '1 was the last rank to be silver .', 'the last total on the chart is the 1 .']
contra  ['1 gold were silver 0 .']
['9 total were listed between 2 and 8 .', '1 nation have at least 8 bronze .', 'its best gold was 0 .', 'the least successful total was 34 .', 'the number of times that 0 `` had been bronze is 5 .', '3 gold have at least a rank of 12 .']
contra  ['the number of times that 2 `` had been bronze is 5 .']
['the total number of nation is 14 .', 'the last silver and its silver is 0 .', '1 was the bronze 4 times .', '7 was the only bronze that had an 7 .', 'there were 5 silver gold 2 .', '11 bronze are not 3 silver .']
contra  ['7 was the bronze 4 times .', '2 was the only bronze that had an 2 .', '11 bronze are not 6 silver .']
['5 total have been total at least 8 times .', '0 total are below 0 in gold .', '2 are the total with at most 1 iraq .', '2 was t

contra  ['1 start of term were a 1813 `` .', 'the number of times 1888 is listed as the start of term is 1 .', "josiah reeve has won 1 sheriff 's ."]
['the total number of tallest base team name fleetwood flyers is 1 .']
contra  ['the total number of tallest base team name leicester super is 1 .']
['listed in article is the only notable riders to have listed in article as its notable riders .', 'there have been 49 total year ended .', 'cleveland park came in base in 1 base .', 'the top base in the table is tongham greyhound stadium .', 'the number of times 2002 appears as the year started is 1 .']
contra  ['wimbledon stadium came in base in 1 base .', 'the number of times 1975 appears as the year started is 1 .']
['the name of the last leagues on this chart is speedway national league, speedway provincial league .', 'the total number of base listed is 49 .']
contra  []
['the total number of team name from speedway national league division two is 2 .', 'kingsmead stadium, canterbury ran

contra  ['the number of position song title missing was 16 .', '339,000 won sales in the song title previous to roll with it .', 'the total amount of times the bjork occurred is 1 .']
['39 position are not sales a 326,000 .', '40 song title are listed in the table .', 'the last song title listed on the record is dreamer .', "stayin' alive represented 1 song title .", 'the total sales of the 960,000 sales was 960000 .', 'the last sales on the chart is the 303,000 .', '37 appears 1 times under the position column .']
contra  ['39 position are not sales a 512,000 .', 'living next door to alice represented 1 song title .', 'the total sales of the 652,000 sales was 960000 .', '14 appears 1 times under the position column .']
['1 sales had 12 position .', "livin' joy is the artist listed last on this chart .", 'the only artist to come out in the position 15 is shaggy .', 'the sales at the top of the list is .', 'the total number of artist listed is 40 .', 'the total number of highest positio

contra  ['for each active ingredient , list which were therapeutic area respiratory .', 'the number of plusvent brand listed is 1 .', '1 pathology had a pathology of pain .']
['the only therapeutic area won therapeutic area dermatology was the dermatology .', 'dermatology had the most in  .', 'the total number of  and  for 9 is 18 .', '11 `` made 1 different therapeutic area .', 'ebastel and others did the brand of the first brand ebastel and others .', '0 therapeutic area have no  .', '1 is the least   .', '4 are  in salmeterol+fluticasone .']
contra  ['the only therapeutic area won therapeutic area gastrointestinal was the gastrointestinal .', 'the total number of  and  for 14 is 18 .', '4 `` made 1 different therapeutic area .', 'tesavel & efficib did the brand of the first brand tesavel & efficib .', '4 are  in almotriptan .']
['the total number of therapeutic area listed in the table is 15 .', '1 therapeutic area almogran and others .', 'the last  on this chart is 15 .', '10 brand

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [136]:
ent = 0
cont = 0
for d in data:
    ent += len(d['extra_entailments'])
    if 'entailments' in d.keys():ent += len(d['entailments'])
    cont += len(d['extra_contradictions'])
    if 'contradictions' in d.keys():cont += len(d['contradictions'])

print(ent, cont, ent+cont)

102022 100818 202840


In [137]:
import json
st = json.dumps(data)
g = open('squall_augment_20_june.json','w')
g.write(st)

35491396

In [138]:
len(data)

11276

In [139]:
count = 0
import shutil

train_json = {}
test_json = {}
for d in data:
    count+=1
    tbl_path = '../WikiTableQuestions/csv/' + d['tbl'].split("_")[0] + '-csv/' + d['tbl'].split("_")[1] + '.csv'
    ent = []
    cont = []
    ent += d['extra_entailments']
    if 'entailments' in d.keys(): ent += d['entailments']
    cont += d['extra_contradictions']
    if 'contradictions' in d.keys(): cont += d['contradictions']
    if count%10==0:
        ## test split
#         table_path = "./squall_v1/test_split/test_csv/"+str(count)+".csv"
#         shutil.copy(tbl_path, table_path)
        key = str(count)+".csv"
        test_json[key] = [
            ent + cont,
            [1]*len(ent) + [0]*len(cont),
            d['title']
        ]
    else:
        ## train split
#         table_path = "./squall_v1/train_split/train_csv/"+str(count)+".csv"
#         shutil.copy(tbl_path, table_path)
        key = str(count)+".csv"
        train_json[key] = [
            ent + cont,
            [1]*len(ent) + [0]*len(cont),
            d['title']
        ]

In [141]:
st1 = json.dumps(train_json)
f = open('./squall_v2/squall_v2/train_split/train_data_new.json','w')
f.write(st1)

st2 = json.dumps(test_json)
g = open('./squall_v2/squall_v2/test_split/test_data_new.json','w')
g.write(st2)

1253898

In [142]:
x = open('./squall_v2/squall_v2/train_split/train_data_new.json','r')
xx = json.load(x)

In [143]:
c = 0
rand = 1
for k,d in xx.items():
    c +=1
    if c == rand: 
        print(k)
        print(d)
        break

1.csv
[['the total number of party on the chart is 38 .', '5 party are ps .', '4 last elected are santiago .', 'the last constituency on this chart is 19 .', 'ps had 2009 last elected .', 'The difference in years between constiuency 1 and 2 is 4 years.', 'The difference in years between constiuency 18 and 2 is 4 years.', 'The difference in years between constiuency 13 and 2 is 0 years.', 'The difference in years between constiuency 16 and 2 is 0 years.', 'The difference in years between constiuency 10 and 2 is 4 years.', 'The difference in years between constiuency 4 and 2 is 0 years.', 'The difference in years between constiuency 12 and 2 is 0 years.', 'The difference in years between constiuency 6 and 2 is 4 years.', 'The difference in years between constiuency 2 and 2 is 0 years.', 'The difference in years between constiuency 1 and 16 is 4 years.', 'The difference in years between constiuency 1 and 8 is 4 years.', 'The difference in years between constiuency 1 and 4 is 4 years.', 'T